In [10]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [11]:
data_desc={
    'model': ['ANI-1ccx', 's66x8', 'ANI-1ccx&s66x8', 'OFF-23'],
    'paths': ['/Users/dominicwelti/Documents/Master_Thesis_Data_Set/Graphite/gridSearch/mace_ani-1ccx.pkl', '/Users/dominicwelti/Documents/Master_Thesis_Data_Set/Graphite/gridSearch/mace_s66x8.pkl', '/Users/dominicwelti/Documents/Master_Thesis_Data_Set/Graphite/gridSearch/mace_ani-1ccx+s66x8.pkl', '/Users/dominicwelti/Documents/Master_Thesis_Data_Set/Graphite/gridSearch/mace-off23.pkl']
}

In [12]:
df_lst=[]
for model, path in zip(data_desc['model'], data_desc['paths']):
    df=pd.read_pickle(path)
    df['Model']=model
    df_lst.append(df)
    print(model,path)

df=pd.concat(df_lst)

ANI-1ccx /Users/dominicwelti/Documents/Master_Thesis_Data_Set/Graphite/gridSearch/mace_ani-1ccx.pkl
s66x8 /Users/dominicwelti/Documents/Master_Thesis_Data_Set/Graphite/gridSearch/mace_s66x8.pkl
ANI-1ccx&s66x8 /Users/dominicwelti/Documents/Master_Thesis_Data_Set/Graphite/gridSearch/mace_ani-1ccx+s66x8.pkl
OFF-23 /Users/dominicwelti/Documents/Master_Thesis_Data_Set/Graphite/gridSearch/mace-off23.pkl


In [13]:
def subset_factors(df):
    df['Total energy']=pd.to_numeric(df['Total energy'])
    df=df.query('2>`Factor a`>0.75 & 2>`Factor c`>0.75')#& `Total energy`<0'
    df.reset_index(drop=True, inplace=True)
    return df

In [14]:
df=subset_factors(df)

In [15]:
def prune(df:pd.DataFrame,precision:float=0.05):
    '''Decrease mesh density to enable plotting of larger area.'''
    sec_a=df['Parameter a'][0]
    sec_c=df['Parameter c'][0]
    drop_lst=[]
    for i, (par_a, par_c) in enumerate(zip(df['Parameter a'],df['Parameter c'])):
        if (sec_a+precision)>par_a>(sec_a-precision):
            if (sec_c+precision)>par_c>(sec_c-precision):
                drop_lst.append(i)
            else:
                sec_c=par_c
        else:
            sec_a=par_a

    return df.drop(index=drop_lst)

In [16]:
df=prune(df)

In [17]:
fig = make_subplots(rows=1,
                    cols=len(data_desc['model']),
                    specs=[len(data_desc['model'])*[{'type': 'scene'}]],
                    subplot_titles=df['Model'].unique()
                    )

for i, model in enumerate(df['Model'].unique()):
    df_sub=df.query(f'Model=="{model}"')
    min_pt = df_sub.iloc[df_sub['Total energy'].argmin()] #data point containing minimum energy
    df_sub=df_sub.query(f"({min_pt['Parameter a']+1}>`Parameter a`>{min_pt['Parameter a']-1}) & ({min_pt['Parameter c']+2}>`Parameter c`>{min_pt['Parameter c']-2}) & `Total energy`<{-4050}")
    #df_sub=df_sub.query(f"`Total energy`<{-4050}")
    fig.add_trace(
        go.Mesh3d(x=df_sub['Parameter a'], y=df_sub['Parameter c'],z=df_sub['Total energy'],
                  opacity=0.8,
                  name=model),
        row=1,
        col=i+1
    )
    fig.add_trace(
        go.Scatter3d(x=[min_pt['Parameter a']],
                    y=[min_pt['Parameter c']],
                    z=[min_pt['Total energy']],
                    marker = dict(
                        size=10,
                        color='red',
                        opacity=0.5),
                    name='Energy minima'
        ),
        row=1,
        col=i+1
    )
    
    fig.update_scenes(
        zaxis=dict(title='Total energy [eV]'), 
        yaxis=dict(title='Lattice parameter c [Å]'),
        xaxis=dict(title='Lattice parameter a [Å]')
    )

fig.update_layout(title='Graphite: grid search for MACE trained potentials',
                  showlegend=False,
                  template='ggplot2'
)

In [18]:
fig.write_html('/Users/dominicwelti/Documents/Master_Thesis_Data_Set/Graphite/gridsearch_02.html')

In [21]:
#fig.write_image('/Users/dominicwelti/Library/CloudStorage/Dropbox/Apps/Overleaf/Master Thesis - MLIP evaluation/graphs/appendix/gridSearch.png',format='png',scale=5)